## Partitioning and formatting of the raw vioscreen information.

This notebook consumes the raw vioscreen data, and splits it up into a series of pivot tables.

The pivot tables are indexed by the survey ID. A survey ID corresponds to a single instance of a vioscreen FFQ. Separate mappings, not included at present, relate the survey ID to a host subject identifier and/or sample barcode.

All headers are scrubbed to avoid annoying characters like spaces. This is done for the benefit of tools like QIIME, however it does reduce readability in some cases.

The v2 notebook includes the output of food items consumption in grams.

A roundtrip test going from raw data to the summarized micro / macronutrients is included at the end of this notebook.

In [27]:
import pandas as pd
import re
import numpy as np
import time
from collections import defaultdict

In [2]:
# full raw vioscreen data
full_vios = pd.read_csv('vioscreen_dump.tsv.gz', sep='\t', dtype=str)

In [3]:
# a raw dump of the ag.source_barcodes_surveys table
survey_sample_map_raw = pd.read_csv('sid_bc.tsv', 
                                    sep='\t', dtype=str).set_index('survey_id')['barcode']
survey_sample_map = defaultdict(list)
for i, s in survey_sample_map_raw.items():
    survey_sample_map[i].append('10317.%s' % s)

In [4]:
def drop_null_cols(df):
    """Drop a column that is entirely null"""
    drop = []
    n = len(df)
    for c in df.columns:
        if df[c].isnull().sum() == n:
            drop.append(c)
    return df.drop(columns=drop)

replacer = re.compile("[ \-,()%':]")
def sanitize_columns(df):
    """Remove possibly annoying characters"""
    df.columns = [replacer.sub('_', c) for c in df.columns]
    return df

def remap_to_sample_id(df):
    new_rows = []
    sample_ids = []
    for _, row in df.reset_index().iterrows():
        for id_ in survey_sample_map.get(row['survey_id'], []):
            new_rows.append(row.copy())
            sample_ids.append(id_)
    new_df = pd.DataFrame(new_rows)
    new_df['#SampleID'] = sample_ids
    return new_df.set_index('#SampleID')

In [5]:
# partition the raw vioscreen data into logically related units.
# within each partition, columns that are entirely null are removed.

# a few specific values are used for this:
# - "code" should correspond to a specific micro/macro nutrient or summarized 
#   value (e.g., % calories from alcohol)
# - "data" contains the raw micro/macro nutrient information for the given food
#   entry for the given survey scaled (I believe) "servingFrequencyText" and the "servingSizeText". 

# where the "code" column is not null
vios_coded = drop_null_cols(full_vios[~full_vios.code.isnull()])

# what should be food components (e.g., % protein)
vios_coded_percents = drop_null_cols(vios_coded[~vios_coded.foodComponentType.isnull()])

# what should be only micro and macronutriet data
vios_coded_micromacro = drop_null_cols(vios_coded[np.logical_and(vios_coded.foodComponentType.isnull(),
                                                                 vios_coded.description != 'Eating Pattern')])

# what vioscreen terms eating patterns (e.g., added fats per day)
vios_coded_eatingpattern = drop_null_cols(vios_coded[vios_coded.description == 'Eating Pattern'])

# entries that are not coded
vios_not_coded = drop_null_cols(full_vios[full_vios.code.isnull()])

# contains the raw vioscreen json output (more below)
vios_with_data = drop_null_cols(vios_not_coded[~vios_not_coded.data.isnull()])

# the vioscreen scores (e.g., Total Fruits)
vios_no_data = drop_null_cols(vios_not_coded[vios_not_coded.data.isnull()])

### Formatting food components

In [6]:
vios_coded_percents.head()

amount      code                             description  \
153   15.49482152820182  %protein        Percent of calories from Protein   
154   44.07939989979141      %fat            Percent of calories from Fat   
155   40.42577857200676    %carbo   Percent of calories from Carbohydrate   
156                 0.0  %alcohol        Percent of calories from Alcohol   
157  16.382593411285388   %sfatot  Percent of calories from Saturated Fat   

    foodComponentType precision shortDescription         survey_id units  
153               1.0       0.0          Protein  80043f5209506497     %  
154               1.0       0.0              Fat  80043f5209506497     %  
155               1.0       0.0     Carbohydrate  80043f5209506497     %  
156               1.0       0.0          Alcohol  80043f5209506497     %  
157               1.0       0.0    Saturated Fat  80043f5209506497     %

In [7]:
vios_coded_percents_pivot = vios_coded_percents.pivot(index='survey_id', columns='description', values='amount')
vios_coded_percents_pivot = remap_to_sample_id(sanitize_columns(vios_coded_percents_pivot))
vios_coded_percents_pivot.to_csv('vioscreen_component_percents.tsv', sep='\t', index=True, header=True)

In [8]:
vios_coded_percents_pivot.head()

survey_id Percent_of_calories_from_Added_Sugar  \
#SampleID                                                                
10317.000072291  0000904d9779a86c                   0.5278094148896552   
10317.000107687  000fc7ac57776579                  0.46065971747342294   
10317.000087663  0012cf765bb386ea                   0.8657785646763633   
10317.000030578  001b4c3e1c848f58                    0.864436614273603   
10317.000030579  001b4c3e1c848f58                    0.864436614273603   

                Percent_of_calories_from_Alcohol  \
#SampleID                                          
10317.000072291                4.405707930741896   
10317.000107687                              0.0   
10317.000087663           0.00023962357002141254   
10317.000030578                7.643624875670007   
10317.000030579                7.643624875670007   

                Percent_of_calories_from_Carbohydrate  \
#SampleID                                               
10317.000072291                    27.628189670463787   
10317.000107687                    23.474779328659373   
10317.000087663                      37.5279841722288   
10317.000030578                     38.41905488083203   
10317.000030579                     38.41905488083203   

                Percent_of_calories_from_Fat  \
#SampleID                                      
10317.000072291           45.084477618669254   
10317.000107687           55.745954131731786   
10317.000087663            43.04814628870771   
10317.000030578            41.82753132412285   
10317.000030579            41.82753132412285   

                Percent_of_calories_from_Monounsaturated_Fat  \
#SampleID                                                      
10317.000072291                            20.95621331900778   
10317.000107687                           22.489476549272094   
10317.000087663                           21.854142563950166   
10317.000030578                           21.020284676343078   
10317.000030579                           21.020284676343078   

                Percent_of_calories_from_Polyunsaturated_Fat  \
#SampleID                                                      
10317.000072291                           12.559912015883315   
10317.000107687                            8.219601812309241   
10317.000087663                              10.351928530673   
10317.000030578                              8.6645383097221   
10317.000030579                              8.6645383097221   

                Percent_of_calories_from_Protein  \
#SampleID                                          
10317.000072291               22.881624780125065   
10317.000107687                20.77926653960884   
10317.000087663                19.42362991549346   
10317.000030578               12.109788919375113   
10317.000030579               12.109788919375113   

                Percent_of_calories_from_Saturated_Fat  
#SampleID                                               
10317.000072291                     10.631030850565056  
10317.000107687                     22.733751192146702  
10317.000087663                      9.169527931007428  
10317.000030578                     11.298838478082244  
10317.000030579                     11.298838478082244

### Formatting micro and macro nutrients

NOTE: headers are augmented to include the unit of measurement (e.g., grams).

In [16]:
vios_coded_micromacro.head()

amount      code                               description  \
0  80.4870014190674  acesupot                      Acesulfame Potassium   
1  23.9946937142986  addsugar  Added Sugars (by Available Carbohydrate)   
2   22.221421156844  adsugtot            Added Sugars (by Total Sugars)   
3  2.82355429149195   alanine                                   Alanine   
4               0.0   alcohol                                   Alcohol   

          survey_id units valueType  \
0  80043f5209506497    mg    Amount   
1  80043f5209506497     g    Amount   
2  80043f5209506497     g    Amount   
3  80043f5209506497     g    Amount   
4  80043f5209506497     g    Amount   

                           description_augmented  
0                     Acesulfame Potassium_in_mg  
1  Added Sugars (by Available Carbohydrate)_in_g  
2            Added Sugars (by Total Sugars)_in_g  
3                                   Alanine_in_g  
4                                   Alcohol_in_g

In [10]:
vios_coded_micromacro = vios_coded_micromacro.copy()
vios_coded_micromacro['description_augmented'] = ["%s_in_%s" % (desc, u)
                                                  for desc, u in zip(vios_coded_micromacro['description'],
                                                                     vios_coded_micromacro['units'])]
vios_coded_micromacro_pivot = vios_coded_micromacro.pivot(index='survey_id', 
                                                          columns='description_augmented', 
                                                          values='amount')
vios_coded_micromacro_pivot = remap_to_sample_id(sanitize_columns(vios_coded_micromacro_pivot))
vios_coded_micromacro_pivot.to_csv('vioscreen_micromacro.tsv', sep='\t', index=True, header=True)

In [11]:
vios_coded_micromacro_pivot.head()

survey_id 3_Methylhistidine_in_mg  \
#SampleID                                                   
10317.000072291  0000904d9779a86c        27.1747373814452   
10317.000107687  000fc7ac57776579        28.2962962869096   
10317.000087663  0012cf765bb386ea        18.2712649474405   
10317.000030578  001b4c3e1c848f58        2.60684169804397   
10317.000030579  001b4c3e1c848f58        2.60684169804397   

                Acesulfame_Potassium_in_mg  \
#SampleID                                    
10317.000072291                        0.0   
10317.000107687                        0.0   
10317.000087663                        0.0   
10317.000030578                        0.0   
10317.000030579                        0.0   

                Added_Sugars__by_Available_Carbohydrate__in_g  \
#SampleID                                                       
10317.000072291                              13.4562635816126   
10317.000107687                              12.5258816620258   
10317.000087663                              20.7296489630817   
10317.000030578                              25.4372404710912   
10317.000030579                              25.4372404710912   

                Added_Sugars__by_Total_Sugars__in_g      Alanine_in_g  \
#SampleID                                                               
10317.000072291                    12.4120058199281  5.51489136698938   
10317.000107687                    11.6483954938307  6.42827878920708   
10317.000087663                    15.8732604976236  3.50057925906138   
10317.000030578                    20.4762200586827  2.14788575606249   
10317.000030579                    20.4762200586827  2.14788575606249   

                         Alcohol_in_g  \
#SampleID                               
10317.000072291      12.3349310056407   
10317.000107687                   0.0   
10317.000087663  0.000514735905194579   
10317.000030578      17.7944461190833   
10317.000030579      17.7944461190833   

                Alpha_Carotene__provitamin_A_carotenoid__in_mcg  \
#SampleID                                                         
10317.000072291                                1138.36933677242   
10317.000107687                                3101.36641244233   
10317.000087663                                565.525633238059   
10317.000030578                                2840.69044111298   
10317.000030579                                2840.69044111298   

                Alpha_Tocopherol_in_mg Animal_Protein_in_g  ...  \
#SampleID                                                   ...   
10317.000072291       28.5702428804122    65.1852377337893  ...   
10317.000107687       15.1735223541489    94.5589348006414  ...   
10317.000087663        15.836220214478    39.3703097824671  ...   
10317.000030578       11.3451129336108    16.6596165030072  ...   
10317.000030579       11.3451129336108    16.6596165030072  ...   

                Vitamin_D__calciferol__in_mcg  \
#SampleID                                       
10317.000072291              12.4742957697532   
10317.000107687               8.9346003949231   
10317.000087663              2.22169212308429   
10317.000030578              3.58194392826441   
10317.000030579              3.58194392826441   

                Vitamin_D2__ergocalciferol__in_mcg  \
#SampleID                                            
10317.000072291                  0.200216711868774   
10317.000107687                                0.0   
10317.000087663                                0.0   
10317.000030578                   1.31924199302752   
10317.000030579                   1.31924199302752   

                Vitamin_D3__cholecalciferol__in_mcg   Vitamin_D_in_IU  \
#SampleID                                                               
10317.000072291                    12.2740790684938  498.971830790127   
10317.000107687                     8.9346003949231  357.384015796924   
10317.000087663                    2.22169212308429  88.867684

### Formatting eating patterns

NOTE: headers are augmented to include the time unit (e.g., per day).

In [14]:
vios_coded_eatingpattern.head()

amount           code     description         survey_id  \
201  6.83359985351562      ADDEDFATS  Eating Pattern  80043f5209506497   
202               0.0    ALCOHOLSERV  Eating Pattern  80043f5209506497   
203  1.24581536668154  ANIMALPROTEIN  Eating Pattern  80043f5209506497   
204   1.8388000404998  CALCDAIRYSERV  Eating Pattern  80043f5209506497   
205   3.4041772177448       CALCSERV  Eating Pattern  80043f5209506497   

      units valueType        code_augmented  
201  PerDay    Amount      ADDEDFATS_PerDay  
202  PerDay    Amount    ALCOHOLSERV_PerDay  
203  PerDay    Amount  ANIMALPROTEIN_PerDay  
204  PerDay    Amount  CALCDAIRYSERV_PerDay  
205  PerDay    Amount       CALCSERV_PerDay

In [13]:
vios_coded_eatingpattern = vios_coded_eatingpattern.copy()
vios_coded_eatingpattern['code_augmented'] = ['%s_%s' % (c, u)
                                              for c, u in zip(vios_coded_eatingpattern['code'],
                                                              vios_coded_eatingpattern['units'])]
vios_coded_eatingpattern_pivot = vios_coded_eatingpattern.pivot(index='survey_id', 
                                                                columns='code_augmented', 
                                                                values='amount')
vios_coded_eatingpattern_pivot = remap_to_sample_id(sanitize_columns(vios_coded_eatingpattern_pivot))
vios_coded_eatingpattern_pivot.to_csv('vioscreen_eatingpatterns.tsv', sep='\t', index=True, header=True)

In [15]:
vios_coded_eatingpattern_pivot.head()

survey_id  ADDEDFATS_PerDay ALCOHOLSERV_PerDay  \
#SampleID                                                                
10317.000072291  0000904d9779a86c  13.7111325807085  0.811984630480205   
10317.000107687  000fc7ac57776579  16.9556567945546                0.0   
10317.000087663  0012cf765bb386ea   10.460175704561                0.0   
10317.000030578  001b4c3e1c848f58   9.4877522015245   1.18359554067103   
10317.000030579  001b4c3e1c848f58   9.4877522015245   1.18359554067103   

                ANIMALPROTEIN_PerDay CALCDAIRYSERV_PerDay   CALCSERV_PerDay  \
#SampleID                                                                     
10317.000072291     3.12011660969654    0.588968275238422  2.43930048364662   
10317.000107687     5.55031021924401     1.02710044945619  2.85550994853688   
10317.000087663     1.75556821008173    0.143241657294231   1.7933502932502   
10317.000030578     1.35898643631758    0.508965186039879  2.37677246201077   
10317.000030579     1.35898643631758    0.508965186039879  2.37677246201077   

                   FISHSERV_PerWeek FRIEDFISH_PerWeek    FRTSUMM_PerDay  \
#SampleID                                                                 
10317.000072291   0.757184681663774               0.0   3.9613478141107   
10317.000107687   0.429514730793156               0.0  1.09213853647856   
10317.000087663                 0.0               0.0  3.27800895759504   
10317.000030578  0.0330395946763966               0.0  1.45998473791023   
10317.000030579  0.0330395946763966               0.0  1.45998473791023   

                  GRAINSERV_PerDay  JUICESERV_PerDay LOWFATDAIRYSERV_PerDay  \
#SampleID                                                                     
10317.000072291  0.203613660210178  1.56846226815002       0.10680657461898   
10317.000107687  0.547190726293276               0.0      0.373823011166429   
10317.000087663                0.0               0.0     0.0412194728851318   
10317.000030578   1.76516303281359               0.0       0.10680657461898   
10317.000030579   1.76516303281359               0.0       0.10680657461898   

                NOFRYFISHSERV_PerWeek NONFATDAIRY_PerDay PLANTPROTEIN_PerDay  \
#SampleID                                                                      
10317.000072291     0.757184681663774                0.0   0.788205997952043   
10317.000107687     0.429514730793156                0.0                 0.0   
10317.000087663                   0.0                0.0  0.0961474784433025   
10317.000030578    0.0330395946763966                0.0   0.712004397299192   
10317.000030579    0.0330395946763966                0.0   0.712004397299192   

                 SALADSERV_PerDay    SOYFOODS_PerDay    VEGSUMM_PerDay  
#SampleID                                                               
10317.000072291  4.27983387202433  0.019353452018679  6.78067953556929  
10317.000107687  1.05764470002423                0.0  8.40219293535005  
10317.000087663  6.61006004091812  0.202395007014275  8.88691729763619  
10317.000030578  2.13061859428066  0.450974494893012  5.41913946629678  
10317.000030579  2.13061859428066  0.450974494893012  5.41913946629678

### Formatting vioscreen scores

NOTE: a "bounds" file is also produced here as vioscreen provides upper and lower limits.

In [17]:
vios_no_data.head()

lowerLimit              name               score         survey_id  \
227        0.0  Total Vegetables  2.3880099595267104  80043f5209506497   
228        0.0  Greens and Beans                 0.0  80043f5209506497   
229        0.0       Total Fruit                 5.0  80043f5209506497   
230        0.0       Whole Fruit                 5.0  80043f5209506497   
231        0.0      Whole Grains  5.6810242143311065  80043f5209506497   

                type upperLimit  
227  TotalVegetables        5.0  
228   GreensAndBeans        5.0  
229       TotalFruit        5.0  
230       WholeFruit        5.0  
231      WholeGrains       10.0

In [18]:
vios_no_data_pivot = vios_no_data.pivot(index='survey_id', columns='type', values='score')
vios_no_data_pivot = remap_to_sample_id(sanitize_columns(vios_no_data_pivot))
vios_no_data_pivot.to_csv('vioscreen_scores.tsv', sep='\t', index=True, header=True)

vios_no_data_pivot_desc = vios_no_data[['type', 'lowerLimit', 'upperLimit']]
vios_no_data_pivot_desc = vios_no_data_pivot_desc[~vios_no_data_pivot_desc.duplicated()]
vios_no_data_pivot_desc = sanitize_columns(vios_no_data_pivot_desc)
vios_no_data_pivot_desc.to_csv('vioscreen_scores_bounds.tsv', sep='\t', index=False, header=True)

In [19]:
vios_no_data_pivot.head()

survey_id               Dairy       EmptyCalories  \
#SampleID                                                                   
10317.000072291  0000904d9779a86c   2.773913251852978                20.0   
10317.000107687  000fc7ac57776579  3.4494368436822747  10.414684587341299   
10317.000087663  0012cf765bb386ea  0.7657591447261929                20.0   
10317.000030578  001b4c3e1c848f58   3.744019504399623                20.0   
10317.000030579  001b4c3e1c848f58   3.744019504399623                20.0   

                         FattyAcids GreensAndBeans RefinedGrains  \
#SampleID                                                          
10317.000072291                10.0            5.0          10.0   
10317.000107687  1.0945527410632858            5.0          10.0   
10317.000087663                10.0            5.0          10.0   
10317.000030578                10.0            5.0          10.0   
10317.000030579                10.0            5.0          10.0   

                SeafoodAndPlantProteins              Sodium  \
#SampleID                                                     
10317.000072291                     5.0  2.9116395144107985   
10317.000107687                     5.0                 0.0   
10317.000087663                     5.0                 0.0   
10317.000030578                     5.0                 0.0   
10317.000030579                     5.0                 0.0   

                         TotalFruit TotalProteins         TotalScore  \
#SampleID                                                              
10317.000072291                 5.0           5.0  76.42011495192892   
10317.000107687  1.4900690155742815           5.0  51.00709571319465   
10317.000087663                 5.0           5.0  70.76575914472619   
10317.000030578  2.8927585756303893           5.0  79.09795635014056   
10317.000030579  2.8927585756303893           5.0  79.09795635014056   

                TotalVegetables         WholeFruit         WholeGrains  
#SampleID                                                               
10317.000072291             5.0                5.0  0.7345621856651521  
10317.000107687             5.0  2.965681423347652  1.5926711021858588  
10317.000087663             5.0                5.0                 0.0  
10317.000030578             5.0                5.0   7.461178270110556  
10317.000030579             5.0                5.0   7.461178270110556

### Format frequency information on the foods consumed

NOTE: two entries are unexpectedly duplicated and are removed.

In [20]:
vios_with_data.head()

amount consumptionAdjustment                  created  \
218    3.0                   1.0  2017-07-29T06:56:24.553   
219    2.0                   1.0  2017-07-29T06:56:24.553   
220    1.0                   1.0  2017-07-29T06:56:24.553   
221    1.5                   1.0  2017-07-29T06:56:24.553   
222    1.0                   1.0  2017-07-29T06:56:24.553   

                                                  data  \
218  [{'code': 'acesupot', 'description': 'Acesulfa...   
219  [{'code': 'acesupot', 'description': 'Acesulfa...   
220  [{'code': 'acesupot', 'description': 'Acesulfa...   
221  [{'code': 'acesupot', 'description': 'Acesulfa...   
222  [{'code': 'acesupot', 'description': 'Acesulfa...   

                                           description foodCode  \
218                             Enchiladas and tamales    40076   
219                 Fresh garlic, including in cooking    30043   
220  Lard, bacon fat or meat drippings (Fat used in...    10005   
221  Meal replacement drinks and shakes such as Sli...    90015   
222  Other candy, such as Lifesavers, licorice and ...    80015   

                                            foodGroup frequency  \
218                      Asian, Mexican and Soy Foods     286.0   
219                             Sauces and Seasonings     365.0   
220                        Oil or Fat Used in Cooking    1460.0   
221  Meal Replacement Drinks, Sports and Granola Bars     365.0   
222                                            Sweets     104.0   

    servingFrequencyText                                    servingSizeText  \
218         5-6 per week                            3 enchiladas or tamales   
219            1 per day                                           2 cloves   
220            4 per day                                        2 teaspoons   
221            1 per day                                 1 1/2 cups (12 oz)   
222           2 per week  4 pieces hard candy, 10 Life Savers<SUP>&reg;<...   

            survey_id  
218  80043f5209506497  
219  80043f5209506497  
220  80043f5209506497  
221  80043f5209506497  
222  80043f5209506497

In [21]:
duplicated = []
for i, grp in vios_with_data.groupby('survey_id'):
    if len(grp.description) != len(grp.description.unique()):
        print(i)
        for d, dup in grp.groupby('description'):
            if len(dup) > 1:
                duplicated.append(dup)

847b5821f05f211f
d95b890fe63c21d0


In [22]:
duplicated[0]

amount consumptionAdjustment                  created  \
1016257    0.5                   1.0  2018-05-09T15:52:12.827   
1016259  0.666                   0.5  2018-05-09T15:52:12.827   

                                                      data  \
1016257  [{'code': 'acesupot', 'description': 'Acesulfa...   
1016259  [{'code': 'acesupot', 'description': 'Acesulfa...   

                                             description foodCode  \
1016257  Soy milk, not fortified (Milk on cooked cereal)   120561   
1016259  Soy milk, not fortified (Milk on cooked cereal)   120561   

                  foodGroup frequency servingFrequencyText servingSizeText  \
1016257  Cereals and Breads      52.0           1 per week  1/2 cup (4 oz)   
1016259  Cereals and Breads      52.0           1 per week         2/3 cup   

                survey_id  
1016257  847b5821f05f211f  
1016259  847b5821f05f211f

In [23]:
duplicated[1]

amount consumptionAdjustment                 created  \
459488    0.5                   1.0  2017-07-29T02:28:12.49   
459489  0.666                   1.0  2017-07-29T02:28:12.49   

                                                     data  \
459488  [{'code': 'acesupot', 'description': 'Acesulfa...   
459489  [{'code': 'acesupot', 'description': 'Acesulfa...   

                                            description foodCode  \
459488  Soy milk, not fortified (Milk on cooked cereal)   120561   
459489  Soy milk, not fortified (Milk on cooked cereal)   120561   

                 foodGroup frequency servingFrequencyText servingSizeText  \
459488  Cereals and Breads     104.0         2-6 per week  1/2 cup (4 oz)   
459489  Cereals and Breads     104.0         2-6 per week         2/3 cup   

               survey_id  
459488  d95b890fe63c21d0  
459489  d95b890fe63c21d0

In [24]:
# manually ignoring the duplicated index values above,
# otherwise would need to filter by grouped survey ids and that seems
# excessive for such a small impact (and likely bug on vioscreens side)
vios_with_data_nodup = vios_with_data.loc[[i for i in vios_with_data.index if i not in [1016259, 459489]]]

# "frequency" is almost certainly the number of instances estimated per year.
# For example, when someone consumes tea once per day, the frequency is 365 whereas
# once per week it is 52. 
vios_with_data_nodup_pivot = vios_with_data_nodup.pivot(index='survey_id', 
                                                        columns='description', 
                                                        values='frequency').fillna(0.0)

vios_with_data_nodup_pivot = remap_to_sample_id(sanitize_columns(vios_with_data_nodup_pivot))
vios_with_data_nodup_pivot.to_csv('vioscreen_foods_consumed_frequency_units_per_year.tsv', sep='\t',
                                  index=True, header=True)

In [25]:
vios_with_data_nodup_pivot.head()

survey_id  \
#SampleID                           
10317.000072291  0000904d9779a86c   
10317.000107687  000fc7ac57776579   
10317.000087663  0012cf765bb386ea   
10317.000030578  001b4c3e1c848f58   
10317.000030579  001b4c3e1c848f58   

                All_other_beans_such_as_baked_beans__lima_beans_and_chili_without_meat  \
#SampleID                                                                                
10317.000072291                                                  0                       
10317.000107687                                                  0                       
10317.000087663                                               52.0                       
10317.000030578                                              182.0                       
10317.000030579                                              182.0                       

                All_other_cheese__such_as_American__cheddar_or_cream_cheese__including_cheese_used_in_cooking  \
#SampleID                                                                                                       
10317.000072291                                              182.0                                              
10317.000107687                                              104.0                                              
10317.000087663                                                  0                                              
10317.000030578                                              104.0                                              
10317.000030579                                              104.0                                              

                All_other_fruits  \
#SampleID                          
10317.000072291             52.0   
10317.000107687                0   
10317.000087663                0   
10317.000030578                0   
10317.000030579                0   

                All_other_lunch_meat_such_as_bologna__salami_and_Spam All_tea  \
#SampleID                                                                       
10317.000072291                                                  0          0   
10317.000107687                                                  0     1642.0   
10317.000087663                                                  0          0   
10317.000030578                                                  0      912.0   
10317.000030579                                                  0      912.0   

                Apples__applesauce_and_pears Apricots___dried  \
#SampleID                                                       
10317.000072291                         52.0            182.0   
10317.000107687                         52.0                0   
10317.000087663                         52.0                0   
10317.000030578                        182.0                0   
10317.000030579                        182.0                0   

                Apricots___fresh_or_canned  \
#SampleID                                    
10317.000072291                          0   
10317.000107687                          0   
10317.000087663                          0   
10317.000030578                          0   
10317.000030579                          0   

                Asian_style__stir_fried__noodles_and_rice__such_as_chow_mein__fried_rice_and_pad_Thai  \
#SampleID                                                                                               
10317.000072291                                                  0                                      
10317.000107687                                                  0                                      
10317.000087663                                                  0                                      
10317.000030578                                                  0                                      
10317.000030579                                                  0                                      

     

### Formatting raw food information

This resulting DataFrame is massive at 39M rows at the time of creating this notebook. Each row represents a micro or macronutrients of each food in its corresponding serving size that the person consumed.

Due to the size, this frame is written out compressed (gzip). We are also not remapping to sample ID here as it would replicate a lot of data in what is already a pretty verbose structure.

This DataFrame will be used to get access to the grams information for food items.

**WARNING: the first cell will run for 5-10 minutes**

In [28]:
# an example of loading the data and what the contents look like.
# The "code" values *should* correspond to the non-null code values
# in the full raw file

# WARNING: this will run for 5-10 minutes
items = []
parsed = {}
start = time.time()
for _, row in vios_with_data.iterrows():    
    # we're using a memoization pattern to minimize parsing JSON. 
    # Of the ~250,000 rows in vios_with_data, only about 50,000 have a unique 
    # "data" JSON object. Parsing JSON is relatively expensive and this memoization
    # shaves a pretty large amount of time off.
    datablock = row['data']
    if datablock in parsed:
        data_parsed = parsed[datablock].copy()
    else:
        data_parsed = pd.read_json(datablock.replace("'", '"'), dtype=False, 
                                   convert_axes=False, convert_dates=False)
                                   
        parsed[datablock] = data_parsed
   
    # make sure relevant information about the survey etc are retained
    # some is probably extraneous
    for c in ['survey_id', 
              'description', 
              'frequency', 
              'servingFrequencyText', 
              'servingSizeText', 
              'foodCode']:
        data_parsed[c] = row[c]
    items.append(data_parsed)
meal_data = pd.concat(items, ignore_index=True)
meal_data.set_index('survey_id', inplace=True)
print(time.time() - start)                    

837.9226973056793


In [29]:
meal_data.head()

code             description units    amount valueType  \
survey_id                                                                      
80043f5209506497  acesupot  Enchiladas and tamales    mg  0.000000    Amount   
80043f5209506497  addsugar  Enchiladas and tamales     g  0.000000    Amount   
80043f5209506497  adsugtot  Enchiladas and tamales     g  0.000000    Amount   
80043f5209506497   alanine  Enchiladas and tamales     g  1.905583    Amount   
80043f5209506497   alcohol  Enchiladas and tamales     g  0.000000    Amount   

                 frequency servingFrequencyText          servingSizeText  \
survey_id                                                                  
80043f5209506497     286.0         5-6 per week  3 enchiladas or tamales   
80043f5209506497     286.0         5-6 per week  3 enchiladas or tamales   
80043f5209506497     286.0         5-6 per week  3 enchiladas or tamales   
80043f5209506497     286.0         5-6 per week  3 enchiladas or tamales   
80043f5209506497     286.0         5-6 per week  3 enchiladas or tamales   

                 foodCode  
survey_id                  
80043f5209506497    40076  
80043f5209506497    40076  
80043f5209506497    40076  
80043f5209506497    40076  
80043f5209506497    40076

In [30]:
meal_data.to_csv('vioscreen_expanded_meal_data.tsv.gz', sep='\t', index=True, header=True,
                 compression='gzip')

In [31]:
meal_data.shape

(39486728, 9)

### Format grams information on the foods consumed

NOTE: the same two entries as before that are unexpectedly duplicated and are removed.

In [115]:
# Keep only grams in the meal_data DataFrame and add row number
meal_data_grams = meal_data.loc[meal_data.code=="grams"]
meal_data_grams = meal_data_grams.reset_index()
meal_data_grams.shape

(249916, 10)

In [116]:
duplicated2 = []
for i, grp in meal_data_grams.groupby('survey_id'):
    if len(grp.description) != len(grp.description.unique()):
        print(i)
        for d, dup in grp.groupby('description'):
            if len(dup) > 1:
                duplicated2.append(dup)

847b5821f05f211f
d95b890fe63c21d0


In [117]:
duplicated2[0]

survey_id   code  \
208899  847b5821f05f211f  grams   
208901  847b5821f05f211f  grams   

                                            description units     amount  \
208899  Soy milk, not fortified (Milk on cooked cereal)     -  17.309589   
208901  Soy milk, not fortified (Milk on cooked cereal)     -  11.528186   

       valueType frequency servingFrequencyText servingSizeText foodCode  
208899    Amount      52.0           1 per week  1/2 cup (4 oz)   120561  
208901    Amount      52.0           1 per week         2/3 cup   120561

In [118]:
duplicated2[1]

survey_id   code  \
94713  d95b890fe63c21d0  grams   
94714  d95b890fe63c21d0  grams   

                                           description units     amount  \
94713  Soy milk, not fortified (Milk on cooked cereal)     -  34.619178   
94714  Soy milk, not fortified (Milk on cooked cereal)     -  46.112745   

      valueType frequency servingFrequencyText servingSizeText foodCode  
94713    Amount     104.0         2-6 per week  1/2 cup (4 oz)   120561  
94714    Amount     104.0         2-6 per week         2/3 cup   120561

In [120]:
# manually ignoring the duplicated Row_nb values above,
# otherwise would need to filter by grouped survey ids and that seems
# excessive for such a small impact (and likely bug on vioscreens side)
meal_data_grams_nodup = meal_data_grams.loc[[i for i in meal_data_grams.index if i not in [208901, 94714]]]

# "amount" is the estimated quantity in grams, almost certainly per day.
meal_data_grams_nodup_pivot = meal_data_grams_nodup.pivot(index='survey_id', 
                                                        columns='description', 
                                                        values='amount').fillna(0.0)

meal_data_grams_nodup_pivot = remap_to_sample_id(sanitize_columns(meal_data_grams_nodup_pivot))
meal_data_grams_nodup_pivot.to_csv('vioscreen_foods_consumed_grams_per_day.tsv', sep='\t',
                                  index=True, header=True)

In [121]:
meal_data_grams_nodup_pivot.head()

survey_id  \
#SampleID                           
10317.000072291  0000904d9779a86c   
10317.000107687  000fc7ac57776579   
10317.000087663  0012cf765bb386ea   
10317.000030578  001b4c3e1c848f58   
10317.000030579  001b4c3e1c848f58   

                 All_other_beans_such_as_baked_beans__lima_beans_and_chili_without_meat  \
#SampleID                                                                                 
10317.000072291                                           0.000000                        
10317.000107687                                           0.000000                        
10317.000087663                                          15.172959                        
10317.000030578                                          79.658036                        
10317.000030579                                          79.658036                        

                 All_other_cheese__such_as_American__cheddar_or_cream_cheese__including_cheese_used_in_cooking  \
#SampleID                                                                                                        
10317.000072291                                          28.272329                                               
10317.000107687                                          16.155617                                               
10317.000087663                                           0.000000                                               
10317.000030578                                           8.077808                                               
10317.000030579                                           8.077808                                               

                 All_other_fruits  \
#SampleID                           
10317.000072291         10.601222   
10317.000107687          0.000000   
10317.000087663          0.000000   
10317.000030578          0.000000   
10317.000030579          0.000000   

                 All_other_lunch_meat_such_as_bologna__salami_and_Spam  \
#SampleID                                                                
10317.000072291                                                0.0       
10317.000107687                                                0.0       
10317.000087663                                                0.0       
10317.000030578                                                0.0       
10317.000030579                                                0.0       

                     All_tea  Apples__applesauce_and_pears  Apricots___dried  \
#SampleID                                                                      
10317.000072291     0.000000                     10.191718          5.189409   
10317.000107687  1597.913445                     35.988632          0.000000   
10317.000087663     0.000000                      5.141233          0.000000   
10317.000030578   887.513436                     35.988632          0.000000   
10317.000030579   887.513436                     35.988632          0.000000   

                 Apricots___fresh_or_canned  \
#SampleID                                     
10317.000072291                         0.0   
10317.000107687                         0.0   
10317.000087663                         0.0   
10317.000030578                         0.0   
10317.000030579                         0.0   

                 Asian_style__stir_fried__noodles_and_rice__such_as_chow_mein__fried_rice_and_pad_Thai  \
#SampleID                                                                                                
10317.000072291                                                0.0                                       
10317.000107687                                                0.0                                       
10317.000087663                                                0.0                                       
10317.000030578                                                0.0                                       
10317.000030579      

### Round trip test

Note the codes in the meal data do not have a 1-1 correspondence with the micromacro frame. In that frame, we used the description field which is more human readable than the code.

It also appears that some codes like GLAC are not obviously represented in the micromacro frame. Similarly, there are some entities like animal protein that do not appear in the meal data frame so that may be inferred by vioscreen elsewhere. 

In [372]:
test_survey = '001b4c3e1c848f58'
test = meal_data.loc[test_survey]

In [378]:
test[test.code == 'GLAC']

amount  code  \
survey_id                          
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  1.910150  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  3.096284  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  3.568904  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  1.437427  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.930636  GLAC   
001b4c3e1c848f58  0.164987  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  1.960348  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  2.233787  GLAC   
001b4c3e1c848f58  4.057757  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.544489  GLAC   
001b4c3e1c848f58  0.851028  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.711497  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  1.636527  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
...                    ...   ...   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.702932  GLAC   
001b4c3e1c848f58  0.801028  GLAC   
001b4c3e1c848f58  0.252476  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  1.538358  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.665620  GLAC   
001b4c3e1c848f58  1.336993  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  1.391782  GLAC   
001b4c3e1c848f58  7.016067  GLAC   
001b4c3e1c848f58  0.000000  GLAC   
001b4c3e1c848f58  3.030604  GLAC   
001b4c3e1c848f58  5.485402  GLAC   
001b4c3e1c848f58  3.923203  GLAC   
001b4c3e1c848f58  1.430008  GLAC   
001b4c3e1c848f58  4.556126  GLAC   

                                                        description units  \
survey_id                                                                   
001b4c3e1c848f58  All other cheese, such as American, cheddar or...  unit   
001b4c3e1c848f58                       Apples, applesauce and pears  unit   
001b4c3e1c848f58                              Avocado and guacamole  unit   
001b4c3e1c848f58                                            Bananas  unit   
001b4c3e1c848f58                Beef, pork, ham and lamb - with fat  unit   
001b4c3e1c848f58                                   Beer (all types)  unit   
001b4c3e1c848f58                                           Broccoli  unit   
001b4c3e1c848f58          Burritos, tacos, tostadas and quesadillas  unit   
001b4c3e1c848f58                        Butter (Cereals and Breads)  unit   
001b4c3e1c848f58                                   Carrots - cooked  unit   
001b4c3e1c848f58                                      Carrots - raw  unit   
001b4c3e1c848f58          Cauliflower, cabbage and Brussels sprouts  unit   
001b4c3e1c848f58                  Chocolate, candy bars, and toffee  unit   
001b4c3e1c848f58                      Coffee (not lattes or mochas)  unit   
001b4c3e1c848f58                                           Coleslaw  unit   
001b4c3e1c848f58                        Cookies and cakes - regular  unit   
001b4c3e1c848f58     Whole grain breads, including bagels and rolls  unit   
001b4c3e1c848f58                                               Eggs  unit   
001b4c3e1c848f58                 Fresh garlic, including in cooking  unit   
001b4c3e1c848f58                                     Fresh tomatoes  unit   
001b4c3e1c848f58                                      Gra

In [373]:
test.groupby('code').agg('sum').head(11)

amount
code                 
GLAC        62.397260
GLTC        69.876978
LineGi     336.912520
acesupot     0.000000
addsugar    25.437240
adsugtot    20.476220
alanine      2.147886
alcohol     17.794446
alphacar  2840.690441
alphtoce    12.646316
alphtoco    11.345113

In [375]:
vios_coded_micromacro_pivot[vios_coded_micromacro_pivot.survey_id == test_survey].iloc[0].head(11)

survey_id                                          001b4c3e1c848f58
3_Methylhistidine_in_mg                            2.60684169804397
Acesulfame_Potassium_in_mg                                      0.0
Added_Sugars__by_Available_Carbohydrate__in_g      25.4372404710912
Added_Sugars__by_Total_Sugars__in_g                20.4762200586827
Alanine_in_g                                       2.14788575606249
Alcohol_in_g                                       17.7944461190833
Alpha_Carotene__provitamin_A_carotenoid__in_mcg    2840.69044111298
Alpha_Tocopherol_in_mg                             11.3451129336108
Animal_Protein_in_g                                16.6596165030072
Arginine_in_g                                      2.87293720209445
Name: 10317.000030578, dtype: object

In [376]:
vios_coded_percents_pivot[vios_coded_percents_pivot.survey_id == test_survey].iloc[0]

survey_id                                         001b4c3e1c848f58
Percent_of_calories_from_Added_Sugar             0.864436614273603
Percent_of_calories_from_Alcohol                 7.643624875670007
Percent_of_calories_from_Carbohydrate            38.41905488083203
Percent_of_calories_from_Fat                     41.82753132412285
Percent_of_calories_from_Monounsaturated_Fat    21.020284676343078
Percent_of_calories_from_Polyunsaturated_Fat       8.6645383097221
Percent_of_calories_from_Protein                12.109788919375113
Percent_of_calories_from_Saturated_Fat          11.298838478082244
Name: 10317.000030578, dtype: object